In [1]:
!pip install torch torchvision torchaudio -q
!pip install torch-geometric -q
!pip install dgl -q  # generic DGL (CPU/GPU autodetect)
!pip install torchmetrics==1.4.0.post0 scikit-learn pandas numpy tqdm geopy haversine -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.7/63.7 kB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 25.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.6/8.6 MB 71.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 868.8/868.8 kB 14.5 MB/s eta 0:00:00


In [2]:
# ============================================================
# Cell 1: Imports
# ============================================================
import pandas as pd
import numpy as np
import ast
from collections import defaultdict

import torch
from torch import nn
import torch.nn.functional as F

from tqdm import tqdm
from scipy.sparse import coo_matrix
from scipy.sparse.linalg import svds
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.metrics import pairwise_distances

Data Loading

In [3]:
# ============================================================
# Cell 2: Load CSVs (keep all columns, parse lists/dicts)
# ============================================================
def load_reviews_csv(path: str) -> pd.DataFrame:
    df = pd.read_csv(path)

    def try_literal(x):
        # Safely convert stringified lists/dicts; leave others alone
        try:
            return ast.literal_eval(str(x))
        except Exception:
            return x

    df = df.applymap(try_literal)
    return df

train_df = load_reviews_csv("train_reviews.csv")
val_df = load_reviews_csv("val_reviews.csv")
test_df = load_reviews_csv("test_reviews.csv")

print("train:", train_df.shape)
print("val:",   val_df.shape)
print("test:",  test_df.shape)

/tmp/ipython-input-1520148129.py:5: DtypeWarning: Columns (5) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(path)
/tmp/ipython-input-1520148129.py:14: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df.applymap(try_literal)
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:2: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:3: SyntaxWarning: invalid decimal literal
<unknown>:7: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:1: SyntaxWarning: invalid decimal literal
<unknown>:1:

train: (278388, 37)
val: (34798, 37)
test: (34799, 37)


Feature Building

In [48]:
# ============================================================
# Normalize 'price' column into integer price levels for HGT
# ============================================================

def normalize_price(x):
    # Handle NaN
    if pd.isna(x):
        return 0  # unknown price

    # If it's a number (float or int)
    if isinstance(x, (int, float)):
        return int(x)

    # If it's a string: attempt numeric conversion
    if isinstance(x, str):
        x = x.strip()

        # Like "$$", "$$$", etc. → map to length
        if all(c == '$' for c in x):
            return len(x)

        # If string represents a number, convert
        if x.isdigit():
            return int(x)

        # Otherwise fallback
        return 0

    # Anything else
    return 0

# Apply to train, val, test (to keep consistency)
for df in [train_df, val_df, test_df]:
    df["price"] = df["price"].apply(normalize_price)

In [4]:
# ============================================================
# Cell 3: Build global ID mappings (SAFE) and add u/i columns
# ============================================================
all_users = pd.concat(
    [train_df["user_id"], val_df["user_id"], test_df["user_id"]],
    ignore_index=True
)
all_items = pd.concat(
    [train_df["gmap_id"], val_df["gmap_id"], test_df["gmap_id"]],
    ignore_index=True
)

user2idx = {u: idx for idx, u in enumerate(all_users.unique())}
item2idx = {i: idx for idx, i in enumerate(all_items.unique())}

num_users = len(user2idx)
num_items = len(item2idx)
print("num_users:", num_users, "num_items:", num_items)

for df in [train_df, val_df, test_df]:
    df["u"] = df["user_id"].map(user2idx)
    df["i"] = df["gmap_id"].map(item2idx)

# Train-only view for all feature construction (avoid leakage)
full_df_train = train_df.copy()

num_users: 25841 num_items: 2923


In [5]:
# ============================================================
# Cell 4: Hardened, Normalized Train-only Feature Builder
# ============================================================

import numpy as np
import pandas as pd

# ------------------------------------------------------------
# 4.1 Ensure category is always a list
# ------------------------------------------------------------
for df in [train_df, val_df, test_df]:
    df["category"] = df["category"].apply(lambda x: x if isinstance(x, list) else [])

# TRAIN-ONLY METADATA
df_train = full_df_train.copy()


# ============================================================
# 4.2 GEO FEATURES (latitude, longitude)
# ============================================================
df_train["latitude"]  = pd.to_numeric(df_train["latitude"], errors="coerce")
df_train["longitude"] = pd.to_numeric(df_train["longitude"], errors="coerce")

item_geo = (
    df_train.groupby("i")[["latitude", "longitude"]]
    .mean()                           # average per item
    .reindex(range(num_items))        # ensure full coverage
    .fillna(0.0)
)

# Normalize geo features (z-score)
item_geo = (item_geo - item_geo.mean()) / (item_geo.std() + 1e-6)
item_geo = item_geo.fillna(0.0).astype("float32")


# ============================================================
# 4.3 CATEGORY MULTI-HOT
# ============================================================
from sklearn.preprocessing import MultiLabelBinarizer

cat_lists = df_train.groupby("i")["category"].apply(
    lambda x: x.iloc[0] if isinstance(x.iloc[0], list) else []
)

mlb = MultiLabelBinarizer()
cat_matrix = mlb.fit_transform(cat_lists)

item_cat = (
    pd.DataFrame(cat_matrix, columns=[f"cat_{c}" for c in mlb.classes_], index=cat_lists.index)
    .reindex(range(num_items), fill_value=0)
    .astype("float32")
)

# categories are already 0/1; normalization optional but safe:
# (optional) item_cat  = (item_cat - item_cat.mean()) / (item_cat.std() + 1e-6)


# ============================================================
# 4.4 NUMERIC STATS (avg_rating, num_of_reviews)
# ============================================================

stats = (
    df_train.groupby("i")[["avg_rating", "num_of_reviews"]]
    .first()
    .reindex(range(num_items))
)

stats["avg_rating"]     = pd.to_numeric(stats["avg_rating"], errors="coerce").fillna(0)
stats["num_of_reviews"] = pd.to_numeric(stats["num_of_reviews"], errors="coerce").fillna(0)

# Normalize ratings: center around 3, scale by 2 → range ≈ [-1, +1]
stats["avg_rating"] = (stats["avg_rating"] - 3.0) / 2.0

# Normalize review counts: log transform for stability
stats["num_of_reviews"] = np.log1p(stats["num_of_reviews"])

# z-score normalize stats
stats = (stats - stats.mean()) / (stats.std() + 1e-6)
item_stats = stats.fillna(0).astype("float32")


# ============================================================
# 4.5 MISC TAG FEATURES
# ============================================================
misc_cols = [c for c in df_train.columns if c.startswith("MISC")]

# Extract vocabulary
misc_labels = set()
for col in misc_cols:
    for entry in df_train[col]:
        if isinstance(entry, list):
            misc_labels.update(entry)

misc_labels = sorted(misc_labels)
misc_label2idx = {tag: idx for idx, tag in enumerate(misc_labels)}

# Initialize (num_items, num_misc_labels)
item_misc_np = np.zeros((num_items, len(misc_labels)), dtype="float32")

# Fill MISC tags
for idx, row in df_train.iterrows():
    i = row["i"]
    if not (0 <= i < num_items):
        continue
    for col in misc_cols:
        tags = row[col]
        if isinstance(tags, list):
            for tag in tags:
                j = misc_label2idx.get(tag)
                if j is not None:
                    item_misc_np[i, j] = 1.0

item_misc = pd.DataFrame(item_misc_np, columns=[f"misc_{m}" for m in misc_labels])

# z-score normalize MISC features
# (optional: many models skip normalization for binary one-hot)
if item_misc.values.sum() > 0:
    item_misc = (item_misc - item_misc.mean()) / (item_misc.std() + 1e-6)
item_misc = item_misc.fillna(0).astype("float32")


# ============================================================
# 4.6 Combine ALL item features safely
# ============================================================
item_features_np = np.hstack([
    item_geo.values.astype("float32"),
    item_cat.values.astype("float32"),
    item_stats.values.astype("float32"),
    item_misc.values.astype("float32"),
])

# Final global normalization for stability
item_features_np = (item_features_np - item_features_np.mean(axis=0)) / \
                   (item_features_np.std(axis=0) + 1e-6)

item_features_np = np.nan_to_num(item_features_np, nan=0.0, posinf=0.0, neginf=0.0)

item_features = torch.tensor(item_features_np, dtype=torch.float32)
print("Final item_features shape:", item_features.shape)


Final item_features shape: torch.Size([2923, 538])


In [6]:
# ============================================================
# Cell 5: Train-only user features (home coord, count, avg rating) and normalize
# ============================================================

user_latlon = (
    df_train.groupby("u")[["latitude", "longitude"]]
    .mean()
    .reindex(range(num_users))
    .fillna(0.0)
)

# normalize latitude/longitude
user_latlon = (user_latlon - user_latlon.mean()) / (user_latlon.std() + 1e-6)
user_latlon = user_latlon.fillna(0)

user_review_counts = (
    df_train.groupby("u")["rating"]
    .count()
    .reindex(range(num_users))
    .fillna(0)
)

# log-normalize review counts
user_review_counts = np.log1p(user_review_counts)

# z-score normalize
user_review_counts = (user_review_counts - user_review_counts.mean()) / (user_review_counts.std() + 1e-6)

user_avg_rating = (
    df_train.groupby("u")["rating"]
    .mean()
    .reindex(range(num_users))
    .fillna(3.0)  # neutral rating
)

# normalize: center at 3, divide by 2
user_avg_rating = (user_avg_rating - 3.0) / 2.0

# z-score
user_avg_rating = (user_avg_rating - user_avg_rating.mean()) / (user_avg_rating.std() + 1e-6)

# combine
user_features_np = np.vstack([
    user_latlon["latitude"].values,
    user_latlon["longitude"].values,
    user_review_counts.values,
    user_avg_rating.values
]).T.astype("float32")

user_features_np = np.nan_to_num(user_features_np, nan=0.0, posinf=0.0, neginf=0.0)

user_features = torch.tensor(user_features_np, dtype=torch.float32)
print("Final user_features shape:", user_features.shape)

Final user_features shape: torch.Size([25841, 4])


Diagonstics

In [7]:
print("Any NaNs in item_features:", torch.isnan(item_features).any().item())
print("Any Infs in item_features:", torch.isinf(item_features).any().item())
print("Item feature max/min:", item_features.max(), item_features.min())

print("\nAny NaNs in user_features:", torch.isnan(user_features).any().item())
print("Any Infs in user_features:", torch.isinf(user_features).any().item())
print("User feature max/min:", user_features.max(), user_features.min())

Any NaNs in item_features: False
Any Infs in item_features: False
Item feature max/min: tensor(54.0580) tensor(-4.7510)

Any NaNs in user_features: False
Any Infs in user_features: False
User feature max/min: tensor(4.7317) tensor(-4.7366)


In [8]:
print("GEO NaNs:",    np.isnan(item_geo.values).any())
print("CAT NaNs:",    np.isnan(item_cat.values).any())
print("STATS NaNs:",  np.isnan(item_stats.values).any())
print("MISC NaNs:",   np.isnan(item_misc.values).any())

GEO NaNs: False
CAT NaNs: False
STATS NaNs: False
MISC NaNs: False


In [9]:
print("GEO shape:", item_geo.shape)
print("CAT shape:", item_cat.shape)
print("STATS shape:", item_stats.shape)
print("MISC shape:", item_misc.shape)
print("Expected num_items:", num_items)

GEO shape: (2923, 2)
CAT shape: (2923, 415)
STATS shape: (2923, 2)
MISC shape: (2923, 119)
Expected num_items: 2923


In [10]:
bad_item_mask = torch.isnan(item_features).any(dim=1) | torch.isinf(item_features).any(dim=1)
bad_items = bad_item_mask.nonzero(as_tuple=True)[0]

print("Bad item count:", len(bad_items))
print("Bad item indices:", bad_items[:20])

Bad item count: 0
Bad item indices: tensor([], dtype=torch.int64)


Baseline Model: LightGCN

In [11]:
# ============================================================
# Cell 6: Train graph (user–item bipartite, symmetric) & helpers
# ============================================================
# User nodes: 0..num_users-1
# Item nodes: num_users..num_users+num_items-1

u_train = torch.tensor(train_df["u"].values, dtype=torch.long)
i_train = torch.tensor(train_df["i"].values + num_users, dtype=torch.long)

# make edges bidirectional
edge_index = torch.stack([
    torch.cat([u_train, i_train]),
    torch.cat([i_train, u_train]),
], dim=0)

num_nodes = num_users + num_items
print("edge_index shape:", edge_index.shape, "num_nodes:", num_nodes)

# Positive items per user for TRAIN (for negative sampling)
user_pos_train = full_df_train.groupby("u")["i"].apply(set).to_dict()

def sample_negative(u: int, k: int = 1):
    """Random negative items for user u, using TRAIN positives only."""
    positives = user_pos_train.get(int(u), set())
    negatives = []
    while len(negatives) < k:
        j = np.random.randint(0, num_items)
        if j not in positives:
            negatives.append(j)
    return negatives


edge_index shape: torch.Size([2, 556776]) num_nodes: 28764


In [12]:
# ============================================================
# DEVICE SETUP
# ============================================================
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# Move data tensors to correct device
edge_index = edge_index.to(device)
item_features = item_features.to(device)
user_features = user_features.to(device)

Using device: cuda


In [13]:
# ============================================================
# LightGCN (Device-Safe, Feature-Safe)
# ============================================================

class LightGCN(nn.Module):
    def __init__(self, num_users, num_items, user_feat_dim, item_feat_dim,
                 dim=64, n_layers=3):
        super().__init__()
        self.num_users = num_users
        self.num_items = num_items
        self.dim = dim
        self.n_layers = n_layers

        # Learnable embeddings
        self.user_emb = nn.Embedding(num_users, dim)
        self.item_emb = nn.Embedding(num_items, dim)

        # Feature projections (all trained)
        self.user_feat_proj = nn.Linear(user_feat_dim, dim, bias=False)
        self.item_feat_proj = nn.Linear(item_feat_dim, dim, bias=False)

        nn.init.xavier_uniform_(self.user_emb.weight)
        nn.init.xavier_uniform_(self.item_emb.weight)

    def propagate(self, x, edge_index):
        row, col = edge_index
        deg = torch.bincount(row, minlength=x.size(0)).float()
        deg_inv_sqrt = deg.pow(-0.5)
        deg_inv_sqrt[deg_inv_sqrt == float("inf")] = 0

        norm = deg_inv_sqrt[row] * deg_inv_sqrt[col]
        msg = x[col] * norm.unsqueeze(1)

        out = torch.zeros_like(x)
        out.index_add_(0, row, msg)
        return out

    def forward(self, edge_index):
        # Move embeddings + features to correct device
        user_x = self.user_emb.weight + self.user_feat_proj(user_features)
        item_x = self.item_emb.weight + self.item_feat_proj(item_features)

        x = torch.cat([user_x, item_x], dim=0)
        all_layers = [x]

        for _ in range(self.n_layers):
            x = self.propagate(x, edge_index)
            all_layers.append(x)

        x_final = torch.stack(all_layers, dim=1).mean(dim=1)

        user_gcn = x_final[:self.num_users]
        item_gcn = x_final[self.num_users:]
        return user_gcn, item_gcn

    def predict(self, u, i, user_gcn, item_gcn):
        return (user_gcn[u] * item_gcn[i]).sum(dim=-1)

In [14]:
# ============================================================
# Cell 8: BPR loss & training utilities (with tqdm)
# ============================================================
from tqdm.auto import tqdm
import wandb

def bpr_loss(model, edge_index, batch_users, batch_pos_items):
    user_gcn, item_gcn = model(edge_index)

    neg_items = torch.tensor(
        [sample_negative(int(u))[0] for u in batch_users],
        dtype=torch.long,
        device=device,
    )

    pos_scores = model.predict(batch_users, batch_pos_items, user_gcn, item_gcn)
    neg_scores = model.predict(batch_users, neg_items, user_gcn, item_gcn)

    return -torch.log(torch.sigmoid(pos_scores - neg_scores)).mean()

def train_bpr_model(model, edge_index, train_df, epochs=10, batch_size=1024, lr=1e-3):
    optimizer = torch.optim.Adam(model.parameters(), lr=lr)

    train_users = torch.tensor(train_df["u"].values, dtype=torch.long, device=device)
    train_items = torch.tensor(train_df["i"].values, dtype=torch.long, device=device)

    epoch_losses, batch_losses = [], []

    for epoch in range(epochs):
        perm = torch.randperm(len(train_users), device=device)
        epoch_loss = 0.0

        pbar = tqdm(perm.split(batch_size), desc=f"LightGCN Epoch {epoch+1}/{epochs}")

        for step, idx in enumerate(pbar):
            batch_u = train_users[idx]
            batch_i = train_items[idx]

            loss = bpr_loss(model, edge_index, batch_u, batch_i)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            bl = loss.item()
            batch_losses.append(bl)
            epoch_loss += bl

            pbar.set_postfix({"batch_loss": f"{bl:.4f}", "epoch_loss": f"{epoch_loss:.4f}"})

        epoch_losses.append(epoch_loss)
        print(f"[LightGCN] Epoch {epoch+1}: total_loss={epoch_loss:.4f}")

    return model, epoch_losses, batch_losses


In [15]:
import wandb
wandb.login()

/usr/local/lib/python3.12/dist-packages/notebook/notebookapp.py:191: SyntaxWarning: invalid escape sequence '\/'
  | |_| | '_ \/ _` / _` |  _/ -_)
wandb: (1) Create a W&B account
wandb: (2) Use an existing W&B account
wandb: (3) Don't visualize my results
wandb: Enter your choice:

 2


wandb: You chose 'Use an existing W&B account'
wandb: Logging into https://api.wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: Find your API key here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: leeij (leeisabella) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


True

In [16]:
lightgcn_layers = 4
lightgcn_dim = 32
lightgcn_lr = 5e-4
lightgcn_batch_size = 2048

In [17]:
# ============================================================
# Cell 9: Train baseline LightGCN with W&B tracking
# ============================================================
import wandb

wandb.init(
    project="restaurant-recsys",
    name="LightGCN-normalized",
    config={
        "model": "LightGCN",
        "embedding_dim": lightgcn_dim,
        "layers": lightgcn_layers,
        "epochs": 10,
        "batch_size": lightgcn_batch_size,
        "learning_rate": lightgcn_lr,
        "num_users": num_users,
        "num_items": num_items,
        "item_feature_dim": item_features.shape[1],
        "user_feature_dim": user_features.shape[1],
    }
)

lgcn = LightGCN(
    num_users=num_users,
    num_items=num_items,
    user_feat_dim=user_features.shape[1],
    item_feat_dim=item_features.shape[1],
    dim=lightgcn_dim,
    n_layers=lightgcn_layers
).to(device)

lgcn, epoch_losses, batch_losses = train_bpr_model(
    lgcn,
    edge_index,
    train_df,
    epochs=10,
    batch_size=lightgcn_batch_size,
    lr=lightgcn_lr
)

wandb.finish()

LightGCN Epoch 1/10:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCN] Epoch 1: total_loss=58.1698


LightGCN Epoch 2/10:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCN] Epoch 2: total_loss=49.6646


LightGCN Epoch 3/10:   0%|          | 0/136 [00:00<?, ?it/s]

...

[LightGCN] Epoch 8: total_loss=36.1193


LightGCN Epoch 9/10:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCN] Epoch 9: total_loss=35.0056


LightGCN Epoch 10/10:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCN] Epoch 10: total_loss=33.8877


In [18]:
# ============================================================
# Cell 10: Evaluation metrics and generic evaluator
# ============================================================
def recall_at_k(target, ranked_list, k):
    return int(target in ranked_list[:k])

def ndcg_at_k(target, ranked_list, k):
    if target in ranked_list[:k]:
        rank = ranked_list.index(target) + 1
        return 1.0 / np.log2(rank + 1)
    return 0.0

def mrr_metric(target, ranked_list):
    if target in ranked_list:
        return 1.0 / (ranked_list.index(target) + 1)
    return 0.0

def evaluate_lgcn_like(model, edge_index, eval_df, k=20):
    model.eval()
    with torch.no_grad():
        user_gcn, item_gcn = model(edge_index)

    recalls, ndcgs, mrrs = [], [], []

    for row in tqdm(eval_df.itertuples(), total=len(eval_df)):
        u = int(row.u)
        true_i = int(row.i)

        scores = (user_gcn[u] * item_gcn).sum(dim=1).cpu().numpy()
        ranked_items = list(np.argsort(-scores))

        recalls.append(recall_at_k(true_i, ranked_items, k))
        ndcgs.append(ndcg_at_k(true_i, ranked_items, k))
        mrrs.append(mrr_metric(true_i, ranked_items))

    return {
        "Recall@{}".format(k): float(np.mean(recalls)),
        "NDCG@{}".format(k): float(np.mean(ndcgs)),
        "MRR": float(np.mean(mrrs)),
    }

print("Baseline LightGCN on validation:")
metrics = evaluate_lgcn_like(lgcn, edge_index, val_df, k=20)
metrics


Baseline LightGCN on validation:


  0%|          | 0/34798 [00:00<?, ?it/s]

{'Recall@20': 0.06477383757687223,
 'NDCG@20': 0.02519366990153189,
 'MRR': 0.019098105462312706}

LightGCN Hyperparam Tuning

In [20]:
# ============================================================
# LightGCN Hyperparameter Tuning (Grid Search)
# ============================================================

import pandas as pd
import itertools

# Search spaces (tune as needed)
dim_grid        = [32, 64, 128]        # embedding sizes
layers_grid     = [3, 4]            # number of propagation layers
batch_grid      = [1024, 2048, 4096]   # batch sizes
lr_grid         = [1e-3, 5e-4]         # learning rates
epochs_val      = 5                   # or 20 if you prefer longer training

results_lgcn = []

for dim_val, layers_val, batch_val, lr_val in itertools.product(
        dim_grid, layers_grid, batch_grid, lr_grid):

    print(f"\n=== Training LightGCN (dim={dim_val}, layers={layers_val}, "
          f"batch={batch_val}, lr={lr_val}) ===")

    # Initialize a fresh LightGCN model
    model = LightGCN(
        num_users=num_users,
        num_items=num_items,
        user_feat_dim=user_features.shape[1],
        item_feat_dim=item_features.shape[1],
        dim=dim_val,
        n_layers=layers_val
    ).to(device)

    # Train model
    model, epoch_losses, batch_losses = train_bpr_model(
        model,
        edge_index,
        train_df,
        epochs=epochs_val,
        batch_size=batch_val,
        lr=lr_val
    )

    # Evaluate on validation set
    metrics_val = evaluate_lgcn_like(model, edge_index, val_df, k=20)

    # Store results
    results_lgcn.append({
        "dim": dim_val,
        "layers": layers_val,
        "batch_size": batch_val,
        "lr": lr_val,
        "Recall@20_val": metrics_val["Recall@20"],
        "NDCG@20_val": metrics_val["NDCG@20"],
        "MRR_val": metrics_val["MRR"],
    })

# Build and display results table
lightgcn_tuning_df = pd.DataFrame(results_lgcn)
display(lightgcn_tuning_df.sort_values("Recall@20_val", ascending=False))


=== Training LightGCN (dim=32, layers=3, batch=1024, lr=0.001) ===


LightGCN Epoch 1/5:   0%|          | 0/260 [00:00<?, ?it/s]

[LightGCN] Epoch 1: total_loss=94.1754


LightGCN Epoch 2/5:   0%|          | 0/260 [00:00<?, ?it/s]

[LightGCN] Epoch 2: total_loss=74.2688


...

[LightGCN] Epoch 4: total_loss=19.0876


LightGCN Epoch 5/5:   0%|          | 0/65 [00:00<?, ?it/s]

[LightGCN] Epoch 5: total_loss=17.9262


  0%|          | 0/34798 [00:00<?, ?it/s]

dim  layers  batch_size      lr  Recall@20_val  NDCG@20_val   MRR_val
9    32       4        2048  0.0005       0.062274     0.024071  0.018046
11   32       4        4096  0.0005       0.062130     0.024069  0.017945
21   64       4        2048  0.0005       0.061210     0.023708  0.017901
17   64       3        4096  0.0005       0.061067     0.023068  0.017047
10   32       4        4096  0.0010       0.061009     0.023704  0.017977
23   64       4        4096  0.0005       0.060981     0.023677  0.017873
7    32       4        1024  0.0005       0.060923     0.023527  0.017780
1    32       3        1024  0.0005       0.060808     0.023289  0.017497
5    32       3        4096  0.0005       0.060636     0.023292  0.017430
19   64       4        1024  0.0005       0.060032     0.023212  0.017677
35  128       4        4096  0.0005       0.059917     0.022944  0.017259
22   64       4        4096  0.0010       0.059917     0.023036  0.017485
3    32       3        2048  0.0005       0.059831     0.023210  0.017589
33  128       4        2048  0.0005       0.059716     0.022789  0.017211
8    32       4        2048  0.0010       0.059716     0.023093  0.017583
4    32       3        4096  0.0010       0.059285     0.022839  0.017283
34  128       4        4096  0.0010       0.058739     0.022066  0.016560
6    32       4        1024  0.0010       0.058193     0.022449  0.017253
29  128       3        4096  0.0005       0.058049     0.021937  0.016475
2    32       3        2048  0.0010       0.057963     0.022048  0.016706
20   64       4        2048  0.0010       0.057848     0.022057  0.016838
16   64       3        4096  0.0010       0.057848     0.022022  0.016677
15   64       3        2048  0.0005       0.057302     0.021895  0.016680
13   64       3        1024  0.0005       0.057015     0.021481  0.016225
18   64       4        1024  0.0010       0.056785     0.021461  0.016346
31  128       4        1024  0.0005       0.056411     0.021206  0.016088
27  128       3        2048  0.0005       0.055980     0.020762  0.015577
0    32       3        1024  0.0010       0.055549     0.021093  0.016103
32  128       4        2048  0.0010       0.055348     0.020488  0.015513
28  128       3        4096  0.0010       0.055204     0.020328  0.015280
14   64       3        2048  0.0010       0.054371     0.020474  0.015715
25  128       3        1024  0.0005       0.053049     0.019659  0.014987
30  128       4        1024  0.0010       0.052819     0.019191  0.014513
26  128       3        2048  0.0010       0.051382     0.018829  0.014361
12   64       3        1024  0.0010       0.050434     0.018413  0.014075
24  128       3        1024  0.0010       0.048221     0.017105  0.012921

Now we move to extended models!

LightGCL

In [56]:
dim = 64
layers = 3
epochs = 10
lr = 5e-4

In [57]:
# ============================================================
# LightGCL: SVD Global View + Contrastive Setup (Train-only)
# ============================================================

from scipy.sparse import coo_matrix
from scipy.sparse.linalg import svds
import torch.nn.functional as F

# --- 1. Build implicit matrix from TRAIN ONLY ---
rows = train_df["u"].values
cols = train_df["i"].values
data = np.ones_like(rows, dtype=np.float32)

M_train = coo_matrix((data, (rows, cols)), shape=(num_users, num_items))
print("M_train shape:", M_train.shape)

# --- 2. SVD rank MUST match LightGCN embedding dimension ---
# dim is the embedding dimension you used for LightGCN
k_svd = dim                       # <<< IMPORTANT: match model dimension >>>
k_svd = min(k_svd, min(num_users, num_items) - 1)

U, s, Vt = svds(M_train, k=k_svd)
idx = np.argsort(-s)
U, s, Vt = U[:, idx], s[idx], Vt[idx, :]

Sigma_sqrt = np.sqrt(s)

P_svd = U * Sigma_sqrt          # (num_users, k_svd)
Q_svd = (Vt.T) * Sigma_sqrt     # (num_items, k_svd)

svd_user_emb = torch.tensor(P_svd, dtype=torch.float32, device=device)
svd_item_emb = torch.tensor(Q_svd, dtype=torch.float32, device=device)

print("svd_user_emb:", svd_user_emb.shape)
print("svd_item_emb:", svd_item_emb.shape)

# --- 3. Normalize & detach SVD embeddings for stability ---
svd_u_norm = F.normalize(svd_user_emb, dim=-1).detach()
svd_i_norm = F.normalize(svd_item_emb, dim=-1).detach()

# --- 4. LightGCL hyperparameters (will be tuned later) ---
tau         = 0.03    # temperature (by tuning)
lambda_con  = 0.1    # contrastive weight (by tuning)
lambda_reg  = 1e-4   # L2 weight (on embeddings)


def contrastive_loss(z, z_tilde, tau=0.2):
    """
    InfoNCE loss: z, z_tilde are (N, d) with aligned rows.
    """
    z = F.normalize(z, dim=-1)
    z_tilde = F.normalize(z_tilde, dim=-1)

    logits = z @ z_tilde.T / tau    # (N, N)
    labels = torch.arange(z.size(0), device=z.device)
    return F.cross_entropy(logits, labels)

M_train shape: (25841, 2923)
svd_user_emb: torch.Size([25841, 64])
svd_item_emb: torch.Size([2923, 64])


In [58]:
# ============================================================
# LightGCL: Step function (BPR + Contrastive)
# ============================================================

def lightgcl_step(model, edge_index, batch_users, batch_pos_items):
    # GCN forward
    user_gcn, item_gcn = model(edge_index)

    # Base BPR loss (exactly as LightGCN)
    loss_bpr = bpr_loss(model, edge_index, batch_users, batch_pos_items)

    # Per-user alignment
    u_embed = user_gcn[batch_users]          # (B, d)
    u_svd   = svd_u_norm[batch_users]        # (B, d)

    # Per-item alignment
    i_embed = item_gcn[batch_pos_items]      # (B, d)
    i_svd   = svd_i_norm[batch_pos_items]    # (B, d)

    L_con_u = contrastive_loss(u_embed, u_svd, tau=tau)
    L_con_i = contrastive_loss(i_embed, i_svd, tau=tau)

    # L2 regularization on learnable embeddings
    reg = 0.5 * (
        model.user_emb.weight.norm(2)**2 +
        model.item_emb.weight.norm(2)**2
    )

    return loss_bpr + lambda_con * (L_con_u + L_con_i) + lambda_reg * reg


# ============================================================
# LightGCL: Training loop (no wandb inside)
# ============================================================

def train_lightgcl(model, edge_index, train_df,
                   epochs=5, batch_size=1024, lr=1e-3):
    optimizer = torch.optim.Adam(model.parameters(), lr=lr)

    train_users = torch.tensor(train_df["u"].values, dtype=torch.long, device=device)
    train_items = torch.tensor(train_df["i"].values, dtype=torch.long, device=device)

    epoch_losses, batch_losses = [], []

    for epoch in range(epochs):
        perm = torch.randperm(len(train_users), device=device)
        epoch_loss = 0.0

        pbar = tqdm(perm.split(batch_size), desc=f"LightGCL Epoch {epoch+1}/{epochs}")

        for step, idx in enumerate(pbar):
            batch_u = train_users[idx]
            batch_i = train_items[idx]

            loss = lightgcl_step(model, edge_index, batch_u, batch_i)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            bl = loss.item()
            batch_losses.append(bl)
            epoch_loss += bl

            pbar.set_postfix({
                "batch_loss": f"{bl:.4f}",
                "epoch_loss": f"{epoch_loss:.4f}"
            })

        epoch_losses.append(epoch_loss)
        print(f"[LightGCL] Epoch {epoch+1}: total_loss={epoch_loss:.4f}")

    return model, epoch_losses, batch_losses

In [59]:
# ============================================================
# Train LightGCL with W&B Tracking
# ============================================================

wandb.init(
    project="restaurant-recsys",
    name="LightGCL",
    config={
        "model": "LightGCL",
        "epochs": epochs,
        "batch_size": 2048,
        "lr": lr,
        "embedding_dim": dim,
        "layers": layers
    }
)

lgcl = LightGCN(
    num_users=num_users,
    num_items=num_items,
    user_feat_dim=user_features.shape[1],
    item_feat_dim=item_features.shape[1],
    dim=dim,
    n_layers=layers,
).to(device)

lgcl, lgcl_epoch_losses, lgcl_batch_losses = train_lightgcl(
    lgcl, edge_index, train_df,
    epochs=epochs, batch_size=2048, lr=lr
)

wandb.finish()

LightGCL Epoch 1/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL] Epoch 1: total_loss=283.3623


LightGCL Epoch 2/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL] Epoch 2: total_loss=168.6243


LightGCL Epoch 3/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL] Epoch 3: total_loss=130.2303


LightGCL Epoch 4/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL] Epoch 4: total_loss=111.2008


LightGCL Epoch 5/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL] Epoch 5: total_loss=100.5596


In [ ]:
# ============================================================
# LightGCL Hyperparameter Tuning (grid search)
# ============================================================

import pandas as pd
import itertools

# define search grid
tau_grid        = [0.03, 0.05, 0.1]
lambda_con_grid = [0.03, 0.05, 0.1]
lambda_reg_val  = 1e-4

results = []

for tau_val, lambda_con_val in itertools.product(tau_grid, lambda_con_grid):
    print(f"\n=== Training LightGCL with tau={tau_val}, lambda_con={lambda_con_val} ===")

    # set globals used by lightgcl_step
    tau        = tau_val
    lambda_con = lambda_con_val
    lambda_reg = lambda_reg_val

    # (re)initialize model
    model = LightGCN(
        num_users=num_users,
        num_items=num_items,
        user_feat_dim=user_features.shape[1],
        item_feat_dim=item_features.shape[1],
        dim=dim,
        n_layers=layers,
    ).to(device)

    # train model
    model, epoch_losses, batch_losses = train_lightgcl(
        model, edge_index, train_df,
        epochs=5, batch_size=2048, lr=1e-3
    )

    # evaluate on validation set
    metrics_val = evaluate_lgcn_like(model, edge_index, val_df, k=20)

    run_result = {
        "tau": tau_val,
        "lambda_con": lambda_con_val,
        "Recall@20_val": metrics_val["Recall@20"],
        "NDCG@20_val": metrics_val["NDCG@20"],
        "MRR_val": metrics_val["MRR"],
    }
    results.append(run_result)

# build comparison table
lightgcl_tuning_df = pd.DataFrame(results)
display(lightgcl_tuning_df.sort_values("Recall@20_val", ascending=False))


=== Training LightGCL with tau=0.03, lambda_con=0.03 ===


LightGCL Epoch 1/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL] Epoch 1: total_loss=109.5646


LightGCL Epoch 2/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL] Epoch 2: total_loss=72.2826


...

[LightGCL] Epoch 4: total_loss=134.9018


LightGCL Epoch 5/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL] Epoch 5: total_loss=129.8106


  0%|          | 0/34798 [00:00<?, ?it/s]

tau  lambda_con  Recall@20_val  NDCG@20_val   MRR_val
2  0.03        0.10       0.062475     0.022148  0.016099
5  0.05        0.10       0.059831     0.021619  0.016071
1  0.03        0.05       0.058768     0.020948  0.015437
0  0.03        0.03       0.058653     0.021207  0.015703
8  0.10        0.10       0.056900     0.020328  0.015284
3  0.05        0.03       0.055980     0.020099  0.014980
6  0.10        0.03       0.055118     0.019901  0.014938
4  0.05        0.05       0.055003     0.019647  0.014686
7  0.10        0.05       0.053997     0.019596  0.014872

In [60]:
# ============================================================
# Evaluate LightGCL on validation set + W&B logging
# ============================================================

import wandb

wandb.init(
    project="restaurant-recsys",
    name="LightGCL-eval",
    config={
        "stage": "evaluation",
        "model": "LightGCL"
    }
)

print("Evaluating LightGCL on validation set...\n")

metrics_lgcl_val = evaluate_lgcn_like(lgcl, edge_index, val_df, k=20)

wandb.log({
    "LightGCL/Recall@20_val": metrics_lgcl_val["Recall@20"],
    "LightGCL/NDCG@20_val":  metrics_lgcl_val["NDCG@20"],
    "LightGCL/MRR_val":      metrics_lgcl_val["MRR"],
})

print("LightGCL Validation Results:")
print(metrics_lgcl_val)

wandb.finish()

Evaluating LightGCL on validation set...



  0%|          | 0/34798 [00:00<?, ?it/s]

LightGCL Validation Results:
{'Recall@20': 0.06457267659060865, 'NDCG@20': 0.02288762674160744, 'MRR': 0.016616757289041488}


LightGCL+Geo

In [ ]:
# LightGCL+Geo hyperparameters

beta = 0.1
rho = 0.1  # decay scale for distance
tau=0.1
lambda_con=0.05
lambda_reg_val = 1e-4
mu_geo=0.01

# Radius-aware negatives
R = 0.1        # tune as needed
alpha = 0.75   # popularity exponent

# Geo-smooth neighbors
k_nn = 10
rho_r = 0.1
mu_geo = 0.05

dim = 64
layers = 4
epochs = 5
lr = 5e-4

In [36]:
# ============================================================
# Geo Precomputation for LightGCL+Geo
# ============================================================

from sklearn.metrics import pairwise_distances

# Raw coords from TRAIN (not normalized features)
df_train_geo = full_df_train.copy()
df_train_geo["latitude"]  = pd.to_numeric(df_train_geo["latitude"],  errors="coerce")
df_train_geo["longitude"] = pd.to_numeric(df_train_geo["longitude"], errors="coerce")

# Item coordinates (num_items, 2)
item_coord_df = (
    df_train_geo.groupby("i")[["latitude", "longitude"]]
    .mean()
    .reindex(range(num_items))
    .fillna(0.0)
)
item_coord = item_coord_df.values

# User "home" coordinates (num_users, 2)
user_coord_df = (
    df_train_geo.groupby("u")[["latitude", "longitude"]]
    .mean()
    .reindex(range(num_users))
    .fillna(0.0)
)
user_coord = user_coord_df.values

def geo_distance(u, i):
    du = user_coord[int(u)]
    di = item_coord[int(i)]
    return float(np.linalg.norm(du - di))

item_pop = (
    full_df_train["i"].value_counts()
    .reindex(range(num_items))
    .fillna(0)
    .values
)

user_geo_candidates = {}
for u in range(num_users):
    dists = np.linalg.norm(item_coord - user_coord[u], axis=1)
    mask = dists <= R
    cand = np.where(mask)[0].tolist()
    cand = [j for j in cand if j not in user_pos_train.get(u, [])]
    if not cand:
        cand = [j for j in range(num_items) if j not in user_pos_train.get(u, [])]
    user_geo_candidates[u] = np.array(cand, dtype=int)

def sample_geo_negative(u, k=1):
    cand = user_geo_candidates[int(u)]
    weights = item_pop[cand] ** alpha
    if weights.sum() > 0:
        probs = weights / weights.sum()
    else:
        probs = None
    return np.random.choice(cand, size=k, p=probs, replace=True)

D_items = pairwise_distances(item_coord)
item_neighbors = []
item_neighbor_weights = []

for i in range(num_items):
    idx = np.argsort(D_items[i])[:k_nn + 1]
    idx = idx[1:]
    item_neighbors.append(idx)
    w = np.exp(-D_items[i, idx] / rho_r)
    item_neighbor_weights.append(w)

def geo_smooth_loss(item_gcn):
    loss = 0.0
    for i in range(num_items):
        neigh = item_neighbors[i]
        if len(neigh) == 0:
            continue
        qi = item_gcn[i]
        qj = item_gcn[neigh]
        w = torch.tensor(
            item_neighbor_weights[i], dtype=torch.float32, device=item_gcn.device
        )
        diff = qi.unsqueeze(0) - qj
        loss += (w * (diff ** 2).sum(dim=1)).sum()
    return loss / num_items

def bpr_geo_terms(model, edge_index, batch_users, batch_pos_items):
    user_gcn, item_gcn = model(edge_index)

    # radius-aware negatives
    neg_items_np = np.concatenate(
        [sample_geo_negative(u.item(), 1) for u in batch_users]
    )
    neg_items = torch.tensor(
        neg_items_np, dtype=torch.long, device=batch_users.device
    )

    pos_base = (user_gcn[batch_users] * item_gcn[batch_pos_items]).sum(dim=-1)
    neg_base = (user_gcn[batch_users] * item_gcn[neg_items]).sum(dim=-1)

    pos_d = torch.tensor(
        [geo_distance(u, i) for u, i in zip(batch_users, batch_pos_items)],
        dtype=torch.float32,
        device=pos_base.device,
    )
    neg_d = torch.tensor(
        [geo_distance(u, j) for u, j in zip(batch_users, neg_items)],
        dtype=torch.float32,
        device=neg_base.device,
    )

    pos_score = pos_base + beta * torch.exp(-pos_d / rho)
    neg_score = neg_base + beta * torch.exp(-neg_d / rho)

    loss_bpr_geo = -torch.log(torch.sigmoid(pos_score - neg_score)).mean()
    loss_geo_smooth = geo_smooth_loss(item_gcn)

    return loss_bpr_geo, loss_geo_smooth, user_gcn, item_gcn

In [37]:
# ============================================================
# LightGCL+Geo Step (BPR_geo + Contrastive + Smoothness)
# ============================================================

def lightgcl_geo_step(model, edge_index, batch_users, batch_pos_items):
    # Geo-aware BPR part
    loss_bpr_geo, loss_geo_smooth, user_gcn, item_gcn = bpr_geo_terms(
        model, edge_index, batch_users, batch_pos_items
    )

    # Contrastive alignment (same as LightGCL)
    u_embed = user_gcn[batch_users]
    u_svd   = svd_u_norm[batch_users]

    i_embed = item_gcn[batch_pos_items]
    i_svd   = svd_i_norm[batch_pos_items]

    L_con_u = contrastive_loss(u_embed, u_svd, tau=tau)
    L_con_i = contrastive_loss(i_embed, i_svd, tau=tau)

    reg = 0.5 * (
        model.user_emb.weight.norm(2)**2 +
        model.item_emb.weight.norm(2)**2
    )

    return (
        loss_bpr_geo +
        lambda_con*(L_con_u + L_con_i) +
        mu_geo * loss_geo_smooth +
        lambda_reg * reg
    )


# ============================================================
# LightGCL+Geo Training Loop
# ============================================================

def train_lightgcl_geo(model, edge_index, train_df, epochs=5, batch_size=1024, lr=1e-3):
    optimizer = torch.optim.Adam(model.parameters(), lr=lr)

    train_users = torch.tensor(train_df["u"].values, dtype=torch.long, device=device)
    train_items = torch.tensor(train_df["i"].values, dtype=torch.long, device=device)

    epoch_losses, batch_losses = [], []

    for epoch in range(epochs):

        perm = torch.randperm(len(train_users), device=device)
        epoch_loss = 0.0

        pbar = tqdm(perm.split(batch_size), desc=f"LightGCL+Geo Epoch {epoch+1}/{epochs}")

        for step, idx in enumerate(pbar):
            batch_u = train_users[idx]
            batch_i = train_items[idx]

            loss = lightgcl_geo_step(model, edge_index, batch_u, batch_i)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            bl = loss.item()
            batch_losses.append(bl)
            epoch_loss += bl

            pbar.set_postfix({"batch_loss": f"{bl:.4f}", "epoch_loss": f"{epoch_loss:.4f}"})

            wandb.log({
                "LightGCL_Geo/batch_loss": bl,
                "LightGCL_Geo/epoch": epoch + 1
            })

        epoch_losses.append(epoch_loss)
        wandb.log({"LightGCL_Geo/epoch_loss": epoch_loss})

        print(f"[LightGCL+Geo] Epoch {epoch+1}: total_loss={epoch_loss:.4f}")

    return model, epoch_losses, batch_losses

In [38]:
# ============================================================
# Train LightGCL+Geo with W&B Tracking
# ============================================================

import wandb

wandb.init(
    project="restaurant-recsys",
    name="LightGCL_Geo",
    config={
        "model": "LightGCL_Geo",
        "embedding_dim": dim,
        "layers": layers,
        "epochs": epochs,
        "batch_size": 2048,
        "learning_rate": lr,
        "tau": tau,
        "lambda_con": lambda_con,
        "lambda_reg": lambda_reg,
        "mu_geo": mu_geo,
    }
)

# initialize model
lgcl_geo = LightGCN(
    num_users=num_users,
    num_items=num_items,
    user_feat_dim=user_features.shape[1],
    item_feat_dim=item_features.shape[1],
    dim=dim,
    n_layers=layers,
).to(device)

# train model
lgcl_geo, lgcl_geo_epoch_losses, lgcl_geo_batch_losses = train_lightgcl_geo(
    lgcl_geo,
    edge_index,
    train_df,
    epochs=epochs,
    batch_size=2048,
    lr=lr
)

wandb.finish()

LightGCL+Geo Epoch 1/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL+Geo] Epoch 1: total_loss=356.1305


LightGCL+Geo Epoch 2/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL+Geo] Epoch 2: total_loss=178.7537


LightGCL+Geo Epoch 3/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL+Geo] Epoch 3: total_loss=138.6249


LightGCL+Geo Epoch 4/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL+Geo] Epoch 4: total_loss=124.6087


LightGCL+Geo Epoch 5/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL+Geo] Epoch 5: total_loss=117.6775


In [39]:
# ============================================================
# Evaluate LightGCL+Geo (lgcl_geo) + W&B logging
# ============================================================

import wandb

wandb.init(
    project="restaurant-recsys",
    name="LightGCLgeo-eval",
    config={
        "stage": "evaluation",
        "model": "LightGCL_Geo"
    }
)

print("Evaluating LightGCL+Geo on validation set...\n")

metrics_lgcl_geo_val = evaluate_lgcn_like(lgcl_geo, edge_index, val_df, k=20)

wandb.log({
    "LightGCL_Geo/Recall@20_val": metrics_lgcl_geo_val["Recall@20"],
    "LightGCL_Geo/NDCG@20_val":  metrics_lgcl_geo_val["NDCG@20"],
    "LightGCL_Geo/MRR_val":      metrics_lgcl_geo_val["MRR"],
})

print("LightGCL+Geo Validation Results:")
print(metrics_lgcl_geo_val)

Evaluating LightGCL+Geo on validation set...



  0%|          | 0/34798 [00:00<?, ?it/s]

LightGCL+Geo Validation Results:
{'Recall@20': 0.01603540433358239, 'NDCG@20': 0.004933954405046516, 'MRR': 0.004424272127550581}


In [ ]:
# ============================================================
# Model Comparison Table (Auto-Logged)
# ============================================================

comparison_df = pd.DataFrame({
    "LightGCL":      metrics_lgcl_val,
    "LightGCL+Geo":  metrics_lgcl_geo_val,
}).T  # transpose so rows = models

print("\nModel Comparison Table:")
print(comparison_df)

# Log to W&B as a table
wandb.log({"model_comparison": wandb.Table(dataframe=comparison_df)})

In [ ]:
# Hyperparam tuning

In [40]:
# ============================================================
# LightGCL+Geo Hyperparameter Tuning (Grid Search)
# ============================================================

import pandas as pd
import itertools

# Define search grid
tau_grid        = [0.03, 0.05]          # you can expand to [0.03, 0.05, 0.1]
lambda_con_grid = [0.05, 0.1]           # same structure as LightGCL
mu_geo_grid     = [0.01, 0.05, 0.1]     # typical geo weights
lambda_reg_val  = 1e-4                  # fixed, same as LightGCL

results_geo = []

for tau_val, lambda_con_val, mu_geo_val in itertools.product(
        tau_grid, lambda_con_grid, mu_geo_grid):

    print(f"\n=== Training LightGCL+Geo with "
          f"tau={tau_val}, lambda_con={lambda_con_val}, mu_geo={mu_geo_val} ===")

    # Set GLOBALS used by lightgcl_geo_step
    tau        = tau_val
    lambda_con = lambda_con_val
    mu_geo     = mu_geo_val
    lambda_reg = lambda_reg_val

    # Reinitialize model
    model_geo = LightGCN(
        num_users=num_users,
        num_items=num_items,
        user_feat_dim=user_features.shape[1],
        item_feat_dim=item_features.shape[1],
        dim=dim,
        n_layers=layers,
    ).to(device)

    # Train
    model_geo, epoch_losses, batch_losses = train_lightgcl_geo(
        model_geo, edge_index, train_df,
        epochs=5, batch_size=2048, lr=1e-3
    )

    # Validation evaluation
    metrics_val = evaluate_lgcn_like(model_geo, edge_index, val_df, k=20)

    # Store run results
    run_result = {
        "tau": tau_val,
        "lambda_con": lambda_con_val,
        "mu_geo": mu_geo_val,
        "Recall@20_val": metrics_val["Recall@20"],
        "NDCG@20_val": metrics_val["NDCG@20"],
        "MRR_val": metrics_val["MRR"],
    }

    results_geo.append(run_result)

# Build result table
lightgcl_geo_tuning_df = pd.DataFrame(results_geo)
display(lightgcl_geo_tuning_df.sort_values("Recall@20_val", ascending=False))



=== Training LightGCL+Geo with tau=0.03, lambda_con=0.05, mu_geo=0.01 ===


LightGCL+Geo Epoch 1/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL+Geo] Epoch 1: total_loss=219.3522


LightGCL+Geo Epoch 2/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL+Geo] Epoch 2: total_loss=142.7748


...


=== Training LightGCL+Geo with tau=0.05, lambda_con=0.05, mu_geo=0.05 ===


LightGCL+Geo Epoch 1/5:   0%|          | 0/136 [00:00<?, ?it/s]

[LightGCL+Geo] Epoch 1: total_loss=252.1891


LightGCL+Geo Epoch 2/5:   0%|          | 0/136 [00:00<?, ?it/s]

KeyboardInterrupt: 

Contrasting Models

Real PinSage

In [33]:
# ============================================================
# Random-walk based neighbor sampler for PinSage
# ============================================================
import numpy as np
import torch
from collections import defaultdict

# Build item-item adjacency from co-reviews (undirected)
adj = [set() for _ in range(num_items)]

for u, g in train_df.groupby("u"):
    items = g["i"].values
    items = np.unique(items)
    for a in items:
        for b in items:
            if a != b:
                adj[a].add(b)
                adj[b].add(a)

# Turn sets into lists for faster indexing
adj = [list(neigh) for neigh in adj]

def build_rw_neighbors(
    adj,
    num_items,
    num_walks=10,
    walk_length=5,
    num_neighbors=50,
    seed=42
):
    rng = np.random.RandomState(seed)
    neigh_idx = np.zeros((num_items, num_neighbors), dtype=np.int64)
    neigh_w   = np.zeros((num_items, num_neighbors), dtype=np.float32)

    all_items = np.arange(num_items)

    for i in range(num_items):
        visits = defaultdict(int)

        if len(adj[i]) == 0:
            # no adjacency: fall back to random neighbors
            chosen = rng.choice(all_items[all_items != i], size=num_neighbors, replace=True)
            weights = np.ones_like(chosen, dtype=np.float32)
        else:
            # random walks from item i
            for _ in range(num_walks):
                cur = i
                for _ in range(walk_length):
                    neighs = adj[cur]
                    if not neighs:
                        break
                    nxt = rng.choice(neighs)
                    visits[nxt] += 1
                    cur = nxt

            if len(visits) == 0:
                chosen = rng.choice(all_items[all_items != i], size=num_neighbors, replace=True)
                weights = np.ones_like(chosen, dtype=np.float32)
            else:
                items_vis = np.array(list(visits.keys()))
                counts    = np.array([visits[k] for k in items_vis], dtype=np.float32)
                order = np.argsort(-counts)
                items_vis = items_vis[order]
                counts    = counts[order]

                if len(items_vis) >= num_neighbors:
                    chosen  = items_vis[:num_neighbors]
                    weights = counts[:num_neighbors]
                else:
                    pad_size = num_neighbors - len(items_vis)
                    pad_items = rng.choice(all_items[all_items != i], size=pad_size, replace=True)
                    chosen  = np.concatenate([items_vis, pad_items])
                    weights = np.concatenate([counts, np.ones(pad_size, dtype=np.float32)])

        weights = weights + 1e-8
        weights = weights / weights.sum()

        neigh_idx[i] = chosen
        neigh_w[i]   = weights

    return neigh_idx, neigh_w

print("Building random-walk neighbors for PinSage...")
rw_neigh_idx_np, rw_neigh_w_np = build_rw_neighbors(
    adj,
    num_items,
    num_walks=10,      # you can tune
    walk_length=5,     # you can tune
    num_neighbors=50,  # you can tune
    seed=42
)

rw_neigh_idx = torch.tensor(rw_neigh_idx_np, dtype=torch.long, device=device)
rw_neigh_w   = torch.tensor(rw_neigh_w_np,   dtype=torch.float32, device=device)

print("Random-walk neighbors built:",
      rw_neigh_idx.shape, rw_neigh_w.shape)

Building random-walk neighbors for PinSage...
Random-walk neighbors built: torch.Size([2923, 50]) torch.Size([2923, 50])


In [34]:
# ============================================================
# PinSage with random-walk importance pooling
# ============================================================
import torch.nn as nn
import torch.nn.functional as F

class RWPinSageLayer(nn.Module):
    """
    One PinSage-style layer:
    - importance-weighted neighbor aggregation
    - optional residual from self representation
    """
    def __init__(self, in_dim, out_dim, use_residual=True):
        super().__init__()
        self.proj = nn.Linear(in_dim, out_dim)
        self.use_residual = use_residual

    def forward(self, x, neigh_idx, neigh_w):
        """
        x:           (N, d)
        neigh_idx:   (N, T)
        neigh_w:     (N, T)
        """
        neigh_emb = x[neigh_idx]              # (N, T, d)
        w = neigh_w.unsqueeze(-1)             # (N, T, 1)
        agg = (neigh_emb * w).sum(dim=1)      # (N, d)

        if self.use_residual:
            agg = agg + x

        h = self.proj(agg)
        return F.relu(h)

class RWPinSageEncoder(nn.Module):
    def __init__(self, in_dim, hidden_dim=64, num_layers=2):
        super().__init__()
        self.input_proj = nn.Linear(in_dim, hidden_dim)
        self.layers = nn.ModuleList([
            RWPinSageLayer(hidden_dim, hidden_dim, use_residual=True)
            for _ in range(num_layers)
        ])

    def forward(self, x, neigh_idx, neigh_w):
        h = F.relu(self.input_proj(x))
        for layer in self.layers:
            h = layer(h, neigh_idx, neigh_w)
        return F.normalize(h, dim=1)

class RWPinSageRecommender(nn.Module):
    def __init__(self, in_dim, hidden_dim=64, num_layers=2):
        super().__init__()
        self.encoder = RWPinSageEncoder(in_dim, hidden_dim, num_layers)

    def forward(self, item_x, neigh_idx, neigh_w):
        return self.encoder(item_x, neigh_idx, neigh_w)

In [35]:
# ============================================================
# Train RW-PinSage with BPR
# ============================================================

def train_pinsage_rw(
    item_features,
    neigh_idx,
    neigh_w,
    epochs=5,
    hidden_dim=64,
    num_layers=2,
    batch_size=2048,
    lr=5e-4,
    max_pos_per_user=10,
    max_steps_per_epoch=200
):
    model = RWPinSageRecommender(item_features.size(1), hidden_dim, num_layers).to(device)
    opt = torch.optim.Adam(model.parameters(), lr=lr)

    # user -> list of positive items
    user_pos = train_df.groupby("u")["i"].apply(list).to_dict()
    train_user_ids = np.array(list(user_pos.keys()))

    def sample_triplet(bs):
        users = np.random.choice(train_user_ids, size=bs)
        pos = np.array([np.random.choice(user_pos[u]) for u in users])
        neg = np.random.randint(0, num_items, size=bs)
        return (
            torch.tensor(users, device=device, dtype=torch.long),
            torch.tensor(pos,    device=device, dtype=torch.long),
            torch.tensor(neg,    device=device, dtype=torch.long),
        )

    for ep in range(1, epochs+1):
        total = 0.0
        steps = min(max(1, len(train_df)//batch_size), max_steps_per_epoch)

        for _ in range(steps):
            u, i, j = sample_triplet(batch_size)

            # full-item embeddings for this step
            item_emb = model(item_features, neigh_idx, neigh_w)  # (num_items, d)

            # build user embedding as mean of some positives
            u_np = u.cpu().numpy()
            u_repr_list = []
            for uid in u_np:
                pos_items = user_pos[int(uid)]
                if len(pos_items) > max_pos_per_user:
                    pos_sample = np.random.choice(pos_items, size=max_pos_per_user, replace=False)
                else:
                    pos_sample = pos_items
                u_repr_list.append(item_emb[pos_sample].mean(0))
            u_repr = torch.stack(u_repr_list, dim=0)  # (B, d)

            pos_scores = (u_repr * item_emb[i]).sum(1)
            neg_scores = (u_repr * item_emb[j]).sum(1)

            loss = -F.logsigmoid(pos_scores - neg_scores).mean()

            opt.zero_grad()
            loss.backward()
            opt.step()

            total += loss.detach().item()

        print(f"[RW-PinSage] epoch {ep} loss={total/steps:.4f}")

    return model

In [36]:
# cache user->pos items once
pinsage_user_pos = train_df.groupby("u")["i"].apply(list).to_dict()

def evaluate_pinsage_rw(item_emb, eval_df, k=20):
    recalls, ndcgs, mrrs = [], [], []

    for row in eval_df.itertuples():
        u = int(row.u)
        true_i = int(row.i)

        pos_items = pinsage_user_pos.get(u, [])
        if len(pos_items) == 0:
            continue

        u_emb = item_emb[pos_items].mean(0)
        scores = (u_emb * item_emb).sum(dim=1).cpu().numpy()
        ranked = list(np.argsort(-scores))

        recalls.append(true_i in ranked[:k])
        ndcgs.append(ndcg_at_k(true_i, ranked, k))
        mrrs.append(mrr_metric(true_i, ranked))

    return {
        "Recall@20": float(np.mean(recalls)),
        "NDCG@20": float(np.mean(ndcgs)),
        "MRR": float(np.mean(mrrs)),
    }

In [38]:
rw_pinsage_model = train_pinsage_rw(
    item_features=item_features,
    neigh_idx=rw_neigh_idx,
    neigh_w=rw_neigh_w,
    epochs=5,
    hidden_dim=64,
    num_layers=2,
    batch_size=2048,
    lr=5e-4,
    max_steps_per_epoch=150
)

with torch.no_grad():
    rw_item_emb = rw_pinsage_model(item_features, rw_neigh_idx, rw_neigh_w)

rw_val_metrics = evaluate_pinsage_rw(rw_item_emb, val_df, k=20)
rw_val_metrics

[RW-PinSage] epoch 1 loss=0.5732
[RW-PinSage] epoch 2 loss=0.5546
[RW-PinSage] epoch 3 loss=0.5543
[RW-PinSage] epoch 4 loss=0.5539
[RW-PinSage] epoch 5 loss=0.5545


{'Recall@20': 0.03550006974473427,
 'NDCG@20': 0.012523769525427442,
 'MRR': 0.011089079165404693}

In [ ]:
rw_pinsage_model = train_pinsage_rw(
    item_features=item_features,
    neigh_idx=rw_neigh_idx,
    neigh_w=rw_neigh_w,
    epochs=5,
    hidden_dim=128,
    num_layers=2,
    batch_size=2048,
    lr=5e-4,
    max_steps_per_epoch=200
)

with torch.no_grad():
    rw_item_emb = rw_pinsage_model(item_features, rw_neigh_idx, rw_neigh_w)

rw_val_metrics = evaluate_pinsage_rw(rw_item_emb, val_df, k=20)
rw_val_metrics

[RW-PinSage] epoch 1 loss=0.5700
[RW-PinSage] epoch 2 loss=0.5657
[RW-PinSage] epoch 3 loss=0.5728


LightGCN + HGT

In [ ]:
# ============================================================
# Build Heterogeneous Metadata Graph for HGT
# ============================================================

from torch_geometric.data import HeteroData
from sklearn.preprocessing import LabelEncoder
from torch_geometric.nn import HGTConv

meta = HeteroData()

# Node types
meta["item"].num_nodes = num_items

# ---- categories ----
cat_encoder = LabelEncoder()
flat_cats = []
for cats in train_df["category"]:
    if isinstance(cats, list):
        flat_cats.extend(cats)
flat_cats = list(set(flat_cats))
cat_encoder.fit(flat_cats)
num_cats = len(flat_cats)
meta["cat"].num_nodes = num_cats

# ---- prices ----
prices = sorted(list(set(train_df["price"])))  # price already normalized earlier
price_encoder = {p: idx for idx, p in enumerate(prices)}
meta["price"].num_nodes = len(prices)

# ---- item→category edges ----
src, dst = [], []
for i, g in train_df.groupby("i"):
    cats = g["category"].iloc[0]
    if isinstance(cats, list):
        for c in cats[:3]:
            if c in cat_encoder.classes_:
                src.append(i)
                dst.append(cat_encoder.transform([c])[0])
meta["item", "has_cat", "cat"].edge_index = torch.tensor([src, dst],
                                                          dtype=torch.long,
                                                          device=device)

# ---- item→price edges ----
src, dst = [], []
for i, g in train_df.groupby("i"):
    p = g["price"].iloc[0]
    src.append(i)
    dst.append(price_encoder[p])
meta["item", "has_price", "price"].edge_index = torch.tensor([src, dst],
                                                              dtype=torch.long,
                                                              device=device)

meta = meta.to(device)

# ============================================================
# HGT Item Encoder (PyG >= 2.x API)
# ============================================================

# Let PyG give us (node_types, edge_types)
metadata = meta.metadata()  # (['item','cat','price'], [...])

class HGTItemEncoder(nn.Module):
    def __init__(self, hidden=64, heads=2, layers=2, metadata=None):
        super().__init__()
        self.metadata = metadata
        node_types, edge_types = metadata

        # Embeddings for each node type
        self.emb = nn.ModuleDict({
            ntype: nn.Embedding(meta[ntype].num_nodes, hidden)
            for ntype in node_types
        })
        for ntype in node_types:
            nn.init.xavier_uniform_(self.emb[ntype].weight)

        # HGTConv layers: in_channels is dict; out_channels must be INT
        self.layers = nn.ModuleList()
        for _ in range(layers):
            conv = HGTConv(
                in_channels={ntype: hidden for ntype in node_types},
                out_channels=hidden,          # <- must be int for your PyG
                metadata=metadata,
                heads=heads,
            )
            self.layers.append(conv)

    def forward(self, hetero_graph: HeteroData):
        node_types, _ = self.metadata

        # x_dict: type -> node features
        x_dict = {ntype: self.emb[ntype].weight for ntype in node_types}

        for conv in self.layers:
            x_dict = conv(x_dict, hetero_graph.edge_index_dict)
            x_dict = {k: F.relu(v) for k, v in x_dict.items()}

        return x_dict["item"]  # only item embeddings are needed

In [ ]:
# ============================================================
# LightGCN + HGT Fusion Model
# ============================================================

class LightGCN_HGT(nn.Module):
    def __init__(self, lgcn_model: LightGCN, hgt_hidden: int, metadata):
        super().__init__()
        self.lgcn = lgcn_model
        self.hgt_encoder = HGTItemEncoder(hidden=hgt_hidden,
                                          heads=2,
                                          layers=2,
                                          metadata=metadata)
        self.fuse = nn.Linear(self.lgcn.dim + hgt_hidden, self.lgcn.dim)

    def fused_emb(self):
        # LightGCN embeddings
        user_gcn, item_gcn = self.lgcn(edge_index)
        # HGT item embeddings
        item_hgt = self.hgt_encoder(meta)

        # Fuse along feature dimension
        fused_item = self.fuse(torch.cat([item_gcn, item_hgt], dim=1))
        return user_gcn, fused_item

In [ ]:
# ============================================================
# Training + Evaluation Helpers
# ============================================================

def train_lightgcn_hgt(epochs, dim, hgt_hidden, batch_size, lr):
    # LightGCN backbone
    lgcn_backbone = LightGCN(
        num_users=num_users,
        num_items=num_items,
        user_feat_dim=user_features.shape[1],
        item_feat_dim=item_features.shape[1],
        dim=dim,
        n_layers=3,
    ).to(device)

    model = LightGCN_HGT(
        lgcn_model=lgcn_backbone,
        hgt_hidden=hgt_hidden,
        metadata=metadata,
    ).to(device)

    opt = torch.optim.Adam(model.parameters(), lr=lr)

    train_u = torch.tensor(train_df["u"].values, dtype=torch.long, device=device)
    train_i = torch.tensor(train_df["i"].values, dtype=torch.long, device=device)

    for ep in range(1, epochs + 1):
        perm = torch.randperm(len(train_u), device=device)
        total_loss = 0.0

        for idx in perm.split(batch_size):
            u = train_u[idx]
            pos_i = train_i[idx]
            neg_i = torch.randint(0, num_items, size=pos_i.size(), device=device)

            ue, ie = model.fused_emb()

            pos = (ue[u] * ie[pos_i]).sum(dim=1)
            neg = (ue[u] * ie[neg_i]).sum(dim=1)

            loss = -torch.log(torch.sigmoid(pos - neg)).mean()

            opt.zero_grad()
            loss.backward()
            opt.step()

            total_loss += loss.item()

        print(f"[LightGCN+HGT] Epoch {ep}/{epochs}  loss={total_loss:.4f}")

    return model


def evaluate_lgcn_like_embeddings(user_emb, item_emb, eval_df, k=20):
    recalls, ndcgs, mrrs = [], [], []

    for row in eval_df.itertuples():
        u = int(row.u)
        true_i = int(row.i)

        scores = (user_emb[u] * item_emb).sum(dim=1).cpu().numpy()
        ranked = list(np.argsort(-scores))

        recalls.append(true_i in ranked[:k])
        ndcgs.append(ndcg_at_k(true_i, ranked, k))
        mrrs.append(mrr_metric(true_i, ranked))

    return {
        "Recall@20": float(np.mean(recalls)),
        "NDCG@20": float(np.mean(ndcgs)),
        "MRR": float(np.mean(mrrs)),
    }


def evaluate_lgcn_hgt(model, eval_df, k=20):
    with torch.no_grad():
        u_emb, i_emb = model.fused_emb()
    return evaluate_lgcn_like_embeddings(u_emb, i_emb, eval_df, k)

In [ ]:
# ============================================================
# Grid Search: LightGCN + HGT
# ============================================================

results_hgt = []

dim_grid        = [64, 128]
hgt_hidden_grid = [32, 64]
lr_grid         = [1e-3, 5e-4]
batch_grid      = [1024, 2048]

for d, h, lr, bs in itertools.product(dim_grid, hgt_hidden_grid, lr_grid, batch_grid):
    print(f"\n### LightGCN+HGT dim={d}, hgt_hidden={h}, lr={lr}, batch={bs}")

    model = train_lightgcn_hgt(
        epochs=5,
        dim=d,
        hgt_hidden=h,
        batch_size=bs,
        lr=lr,
    )

    with torch.no_grad():
        u_emb, i_emb = model.fused_emb()

    metrics = evaluate_lgcn_like_embeddings(u_emb, i_emb, val_df, k=20)

    results_hgt.append({
        "dim": d,
        "hgt_hidden": h,
        "lr": lr,
        "batch": bs,
        "Recall@20": metrics["Recall@20"],
        "NDCG@20": metrics["NDCG@20"],
        "MRR": metrics["MRR"],
    })

lghgt_grid = pd.DataFrame(results_hgt)
display(lghgt_grid.sort_values("Recall@20", ascending=False))

In [ ]:
hgt_dim = [64, 128]
hgt_hidden = [32, 64, 128]
hgt_lr = [1e-3, 5e-4]
hgt_batch = [1024, 2048]

In [ ]:
model_hgt = train_lightgcn_hgt(
    epochs=5,
    dim=hgt_dim,
    hgt_hidden=hgt_hidden,
    batch_size=hgt_batch,
    lr=hgt_lr
)

hgt_val_metrics = evaluate_lgcn_hgt(model_hgt, val_df, k=20)
print(hgt_val_metrics)